In [2]:
import numpy as np
import networkx as nx
import plotly

import node2vec

import torch
import torch_geometric as tg

from sklearn.manifold import SpectralEmbedding
from sklearn.cluster import KMeans

In [9]:
def plot_graph(G, pos):
    edge_x = []
    edge_y = []
    for edge in G.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.extend([x0, x1, None])
        edge_y.extend([y0, y1, None])

    edge_trace = plotly.graph_objects.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    node_x = []
    node_y = []
    for node in G.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)

    node_trace = plotly.graph_objects.Scatter(
        x=node_x, y=node_y,
        mode='markers',
        hoverinfo='text',
        marker=dict(
            showscale=True,
            # colorscale options
            #'Greys', 'YlGnBu', 'Greens', 'YlOrRd', 'Bluered', 'RdBu',
            #'Reds', 'Blues', 'Picnic', 'Rainbow', 'Portland', 'Jet',
            #'Hot', 'Blackbody', 'Earth', 'Electric', 'Viridis', 'Cividis'
            colorscale='YlGnBu',
            reversescale=True,
            color=[],
            size=5,
            colorbar=dict(
                thickness=15,
                title='Node Connections',
                xanchor='left',
                titleside='right'
            ),
            line_width=2))

    node_adjacencies = []
    node_text = []
    for node, adjacencies in enumerate(G.adjacency()):
        node_adjacencies.append(len(adjacencies[1]))
        node_text.append(f'#{node+1} has {len(adjacencies[1])} connections')

    node_trace.marker.color = node_adjacencies
    node_trace.text = node_text

    fig = plotly.graph_objects.Figure(data=[edge_trace, node_trace],
            layout=plotly.graph_objects.Layout(
                title='<br>Network graph',
                titlefont_size=16,
                showlegend=False,
                hovermode='closest',
                margin=dict(b=20,l=5,r=5,t=40),
                annotations=[ dict(
                    text="Graph Network",
                    showarrow=False,
                    xref="paper", yref="paper",
                    x=0.005, y=-0.002 ) ],
                xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                yaxis=dict(showgrid=False, zeroline=False, showticklabels=False))
                )

    fig.show()

## Read Data

### AIDS Data
https://networkrepository.com/AIDS.php

In [10]:
G_AIDS = nx.Graph()

with open('data/AIDS/AIDS.edges', 'r') as file:
    for line in file:
        if line.startswith('%'):
            continue
        u, v = map(int, line.strip().split(','))
        G_AIDS.add_edge(u, v)

print(G_AIDS.number_of_nodes(), G_AIDS.number_of_edges())
pos = nx.spring_layout(G_AIDS)

31175 32390


### Fingerprint Data
https://networkrepository.com/Fingerprint.php

In [8]:
G_FP = nx.Graph()

with open('data/Fingerprint/Fingerprint.edges', 'r') as file:
    for line in file:
        if line.startswith('#'):
            continue
        u, v = map(int, line.strip().split(','))
        G_FP.add_edge(u, v)
        print(u, v)

print(G_FP.number_of_nodes(), G_FP.number_of_edges())
pos = nx.spring_layout(G_FP)

1 2
2 1
3 7
7 3
7 8
8 7
8 9
9 8
9 10
10 9
10 11
11 10
11 12
12 11
12 13
13 12
13 6
6 13
4 14
14 4
14 5
5 14
15 16
16 15
17 19
19 17
19 20
20 19
20 18
18 20
21 23
23 21
23 24
24 23
24 25
25 24
25 26
26 25
26 22
22 26
27 31
31 27
31 32
32 31
32 33
33 32
33 34
34 33
34 35
35 34
35 36
36 35
36 30
30 36
28 37
37 28
37 38
38 37
38 39
39 38
39 29
29 39
40 41
41 40
42 46
46 42
46 47
47 46
47 48
48 47
48 49
49 48
49 50
50 49
50 51
51 50
51 44
44 51
43 52
52 43
52 53
53 52
53 54
54 53
54 45
45 54
55 57
57 55
57 58
58 57
58 59
59 58
59 56
56 59
60 62
62 60
62 63
63 62
63 64
64 63
64 65
65 64
65 61
61 65
66 68
68 66
68 69
69 68
69 67
67 69
70 72
72 70
72 73
73 72
73 74
74 73
74 75
75 74
75 71
71 75
76 80
80 76
80 81
81 80
81 82
82 81
82 83
83 82
83 78
78 83
77 84
84 77
84 85
85 84
85 86
86 85
86 87
87 86
87 88
88 87
88 79
79 88
89 90
90 89
91 93
93 91
93 94
94 93
94 95
95 94
95 96
96 95
96 92
92 96
97 101
101 97
101 102
102 101
102 99
99 102
98 103
103 98
103 104
104 103
104 105
105 104
105 106
10

KeyboardInterrupt: 

### FB CMU Data
https://networkrepository.com/fb-CMU-Carnegie49.php

In [3]:
G_EURO_ROAD = nx.Graph()

with open('data/inf-euroroad/inf-euroroad.edges', 'r') as file:
    for line in file:
        if line.startswith('%'):
            continue
        u, v = map(int, line.strip().split())
        G_EURO_ROAD.add_edge(u-1, v-1)

print(G_EURO_ROAD.number_of_nodes(), G_EURO_ROAD.number_of_edges())
pos = nx.spring_layout(G_EURO_ROAD)

1174 1417


In [11]:
G = G_AIDS
plot_graph(G, pos)

In [5]:
EPOCHS = 100
LR = 0.01
NUM_CLASSES_CLUSTERS = 10

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

## Data Preprocessing

In [6]:
edge_index = torch.tensor(list(G.edges)).t().contiguous()
x = torch.eye(G.number_of_nodes())
y = torch.zeros(G.number_of_nodes(), dtype=torch.long)
# y = torch.randint(0, NUM_CLASSES, (G.number_of_nodes(),))
data = tg.data.Data(x=x, edge_index=edge_index)

# generate train, val and test masks
train_mask = torch.zeros(G.number_of_nodes(), dtype=torch.bool)
train_mask[:int(G.number_of_nodes()*0.8)] = 1

val_mask = torch.zeros(G.number_of_nodes(), dtype=torch.bool)
val_mask[int(G.number_of_nodes()*0.8):int(G.number_of_nodes()*0.9)] = 1

test_mask = torch.zeros(G.number_of_nodes(), dtype=torch.bool)
test_mask[int(G.number_of_nodes()*0.9):] = 1

## Graph Convolutional Network

In [ ]:
class GCN(torch.nn.Module):
    def __init__(self, num_node_features, num_classes):
        super(GCN, self).__init__()
        self.conv1 = tg.nn.GCNConv(num_node_features, 64)
        self.conv2 = tg.nn.GCNConv(64, num_classes)

    def forward(self, data):
        x, edge_index = data.x, data.edge_index

        x = self.conv1(x, edge_index)
        x = torch.nn.functional.relu(x)
        x = torch.nn.functional.dropout(x)
        x = self.conv2(x, edge_index)

        return torch.nn.functional.log_softmax(x, dim=1)

In [ ]:
model = GCN(num_node_features=data.num_nodes, num_classes=NUM_CLASSES_CLUSTERS).to(device)
data = data.to(device)
optimizer = torch.optim.Adam(model.parameters(), lr=LR, weight_decay=5e-4)

In [ ]:
for epoch in range(EPOCHS):
    model.train()
    optimizer.zero_grad()
    out = model(data)
    loss = torch.nn.functional.nll_loss(out[train_mask], data.y[train_mask])
    loss.backward()
    optimizer.step()

    # validate the model
    model.eval()
    _, pred = model(data).max(dim=1)
    correct = float(pred[val_mask].eq(data.y[val_mask]).sum().item())
    acc = correct / val_mask.sum().item()
    if (epoch+1) % 10 == 0:
        print(f'Epoch: {epoch+1:03d}\t Loss: {loss:.4f}\t Val Acc: {acc:.4f}')

In [ ]:
# test the model
model.eval()
_, pred = model(data).max(dim=1)
correct = float(pred[test_mask].eq(data.y[test_mask]).sum().item())
acc = correct / test_mask.sum().item()
print(f'Test Acc: {acc:.4f}')

## Unsupervised Graph Convolutional Network

In [ ]:
# create unsupervised graph convolutional neural network model
class GCN(torch.nn.Module):
    def __init__(self, num_features, embedding_dim):
        super(GCN, self).__init__()
        self.conv1 = tg.nn.GCNConv(num_features, 64)
        self.conv2 = tg.nn.GCNConv(64, embedding_dim)

    def forward(self, data):
        x, edge_index = data.x, data.edge_index

        x = self.conv1(x, edge_index)
        x = torch.nn.functional.relu(x)
        # x = self.conv2(x, edge_index)

        # return torch.nn.functional.log_softmax(x, dim=1)
        return self.conv2(x, edge_index)

In [ ]:
def reconstruction_loss(z, edge_index):
    # Compute a pairwise cosine similarity between node embeddings
    adj_reconstructed = torch.sigmoid(torch.matmul(z, z.t()))
    
    # Only consider the edges present in the graph
    adj_ground_truth = torch.zeros_like(adj_reconstructed)
    adj_ground_truth[edge_index[0], edge_index[1]] = 1

    # Use a binary cross-entropy loss
    loss = torch.nn.functional.binary_cross_entropy(adj_reconstructed, adj_ground_truth)
    return loss

In [ ]:
model = GCN(num_features=data.num_nodes, embedding_dim=NUM_CLASSES_CLUSTERS).to(device)
optimizer = torch.optim.Adam(model.parameters(), lr=LR)

for epoch in range(EPOCHS):
    model.train()
    optimizer.zero_grad()
    z = model(data)
    loss = reconstruction_loss(z, data.edge_index)
    loss.backward()
    optimizer.step()

    if (epoch+1) % 10 == 0:
        print(f'Epoch {epoch+1}\t Loss: {loss.item()}')

In [ ]:
# test the model
model.eval()
_, pred = model(data).max(dim=1)
correct = float(pred[test_mask].eq(data.y[test_mask]).sum().item())
acc = correct / test_mask.sum().item()
print(f'Test Acc: {acc:.4f}')

## Graph Encoder Embedding

In [ ]:
class Encoder(torch.nn.Module):
    def __init__(self, num_features, embedding_dim):
        super(Encoder, self).__init__()
        self.conv1 = tg.nn.GCNConv(num_features, 64)
        self.conv2 = tg.nn.GCNConv(64, embedding_dim)

    def forward(self, x, edge_index):
        x = self.conv1(x, edge_index)
        x = torch.relu(x)
        return self.conv2(x, edge_index)

In [ ]:
def decode(embeddings):
    adj_reconstructed = torch.sigmoid(torch.matmul(embeddings, embeddings.t()))
    return adj_reconstructed

In [ ]:
class GAE(torch.nn.Module):
    def __init__(self, encoder):
        super(GAE, self).__init__()
        self.encoder = encoder

    def forward(self, x, edge_index):
        embeddings = self.encoder(x, edge_index)
        return decode(embeddings)

In [ ]:
def loss_function(reconstructed_adj, edge_index):
    # Convert edge_index to adjacency matrix
    adj_original = torch.zeros(reconstructed_adj.shape)
    adj_original[edge_index[0], edge_index[1]] = 1
    
    # Binary cross-entropy loss
    return torch.nn.functional.binary_cross_entropy(reconstructed_adj, adj_original)

In [ ]:
# Initialize model and optimizer
encoder_model = Encoder(data.num_nodes, embedding_dim=NUM_CLASSES_CLUSTERS)
model = GAE(encoder_model)
optimizer = torch.optim.Adam(model.parameters(), lr=LR)

# Training loop
for epoch in range(EPOCHS):
    optimizer.zero_grad()
    reconstructed_adj = model(data.x, data.edge_index)
    loss = loss_function(reconstructed_adj, data.edge_index)
    loss.backward()
    optimizer.step()

    if (epoch+1) % 10 == 0:
        print(f"Epoch {epoch+1}, Loss: {loss.item()}")

## Spectral Embedding

In [7]:
adj_matrix = nx.adjacency_matrix(G).todense()
adj_array = np.asarray(adj_matrix)

embedding = SpectralEmbedding(n_components=2)  # 2D embedding
spectral_embedding = embedding.fit_transform(adj_array)

kmeans = KMeans(n_clusters=NUM_CLASSES_CLUSTERS)
clusters = kmeans.fit_predict(spectral_embedding)

/var/folders/h3/9j390gx10pb67vhwk1f_m4sm0000gn/T/ipykernel_64711/4091280411.py:1: FutureWarning:

adjacency_matrix will return a scipy.sparse array instead of a matrix in Networkx 3.0.

/Users/mahadevmaitri/Downloads/stat622/.venv/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



## Node2Vec

In [ ]:
node2vec = node2vec.Node2Vec(G, dimensions=64, walk_length=30, num_walks=200, workers=4)

model = node2vec.fit(window=10, min_count=1, batch_words=4)

embeddings = model.wv

node_ids = list(G.nodes())  # List of nodes in the graph
embedding_matrix = np.array([model.wv[str(node_id)] for node_id in node_ids])

kmeans = KMeans(n_clusters=NUM_CLASSES_CLUSTERS)
clusters = kmeans.fit_predict(embedding_matrix)